pyLDAvis 는 LDA 모델의 학습 결과를 시각적으로 보여주는 유용한 툴킷입니다. 설치법 및 더 자세한 튜토리얼은 [pyLDAvis의 github][pyldavis]을 들어가셔서 보시기 바랍니다. 

우리는 앞서 학습한 LDA 를 시각화 합니다.

이 과정에서 만들어지는 파일들의 주소를 미리 지정해둡니다.

[pyldavis]: https://github.com/bmabey/pyLDAvis/blob/master/notebooks/pyLDAvis_overview.ipynb

In [1]:
import config
from collections import Counter
from lovit_textmining_dataset.navernews_10days import get_bow

x, idx_to_vocab, vocab_to_idx = get_bow(date='2016-10-20', tokenize='noun')

dictionary_path = './2016-10-20-noun_dictionary.txt'
ldamodel_path = './2016-10-20-lda.pkl'
prepared_data_path = './2016-10-20-pyldavis_prepared_data.pkl'
pyldavis_path = '2016-10-20-pyldavis.html'

soynlp=0.0.491
added lovit_textmining_dataset


LDAVis 는 세 가지 정보를 이용합니다. (1) 학습된 LDA model 과 (2) Corpus, (3) Dictionary 를 이용합니다. Dictionary 는 Gensim 이 이용하는 vocabulary mapper 인데, 이 포멧에 대한 정보는 appendix tutorial (day_6_a_gensim_dictionary_format.ipynb) 을 참고하세요.

Term frequency matrix 에서 nonzero() 의 출력값은 nonzero elements 의 row, column index 입니다. column index 는 각 단어의 index 가 저장되어 있기 때문에 이를 Counter 에 넣으면 document frequency 를 계산할 수 있습니다. 이를 파일로 저장합니다.

In [2]:
df = Counter(x.nonzero()[1])
df = [df.get(i, 0) for i in range(x.shape[1])]

with open(dictionary_path, 'w', encoding='utf-8') as f:
    f.write('{}\n'.format(x.shape[0]))
    for idx, term in enumerate(idx_to_vocab):
        # index, term, df
        f.write('{}\t{}\t{}\n'.format(idx, term, df[idx]))

Dictionary, Corpus, 학습된 LDA model 을 로딩합니다.

In [3]:
import pickle
import gensim

dictionary = gensim.corpora.Dictionary.load_from_text(dictionary_path)
corpus = gensim.matutils.Sparse2Corpus(x, documents_columns=False)
with open(ldamodel_path, 'rb') as f:
    lda = pickle.load(f)

lda 모델이 제대로 로딩되었는지 show_topics()를 이용하여 살펴봅니다

In [4]:
lda.show_topics(num_words=5)

[(8, '0.040*"울산" + 0.030*"방지" + 0.027*"진화" + 0.024*"이동" + 0.024*"디지털"'),
 (35, '0.058*"대출" + 0.050*"부동산" + 0.031*"분양" + 0.026*"시장" + 0.023*"대책"'),
 (20, '0.089*"사고" + 0.044*"기관사" + 0.035*"전동차" + 0.027*"확인" + 0.027*"조사"'),
 (19, '0.039*"승객" + 0.037*"열차" + 0.030*"출입문" + 0.026*"출발" + 0.024*"운전"'),
 (69, '0.075*"행사" + 0.047*"재배포" + 0.043*"서울" + 0.040*"기자" + 0.039*"20일"'),
 (30, '0.507*"무단" + 0.061*"금지" + 0.030*"인턴기자" + 0.012*"스포츠월드" + 0.010*"기자"'),
 (54, '0.063*"한옥" + 0.041*"제주" + 0.020*"주제" + 0.018*"대한민국" + 0.018*"교수"'),
 (6, '0.051*"고문" + 0.046*"사장" + 0.037*"재판" + 0.031*"1심" + 0.030*"상임고문"'),
 (99, '0.113*"주택" + 0.069*"보는" + 0.055*"경제" + 0.046*"금리" + 0.031*"중앙"'),
 (24, '0.023*"회고록" + 0.023*"의원" + 0.018*"송민순" + 0.018*"당시" + 0.018*"답변"')]

pyLDAvis.gensim.prepare()를 이용하면 시각화 할 준비를 합니다. 

In [5]:
import pyLDAvis

print(pyLDAvis.__version__)

/home/lovit/anaconda2/envs/scrapper/lib/python3.6/importlib/_bootstrap.py:205: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


2.1.1


Prepared Data 는 D3 code 에 넘겨줄 JSON 형식의 dataset 입니다.

In [6]:
import pyLDAvis.gensim as gensimvis
prepared_data = gensimvis.prepare(lda, corpus, dictionary)

/home/lovit/anaconda2/envs/scrapper/lib/python3.6/site-packages/pyLDAvis/_prepare.py:387: DeprecationWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/indexing.html#ix-indexer-is-deprecated
  topic_term_dists = topic_term_dists.ix[topic_order]
/home/lovit/anaconda2/envs/scrapper/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  return pd.concat([default_term_info] + list(topic_dfs))


pyLDAvis.display() 를 하면 Bokeh 와 같은 HTML 형식의 interactive 웹페이지가 출력됩니다.

$relevance(w \vert t) = \lambda \times p(w \vert t) + (1 - \lambda) * \frac{p(w \vert t)}{p(w)}$
- w: term
- t: topic

In [7]:
pyLDAvis.display(prepared_data)

Prepared data 역시 pickling 이 가능합니다. 

In [8]:
with open(prepared_data_path, 'wb') as f:
    pickle.dump(prepared_data, f)

loaded_pyldavis 역시 동일하게 시각화가 됩니다. 

In [9]:
import pickle
import pyLDAvis

with open(prepared_data_path, 'rb') as f:
    loaded_prepared_data = pickle.load(f)
pyLDAvis.display(loaded_prepared_data)

html 로 저장이 가능합니다.

In [10]:
pyLDAvis.save_html(prepared_data, pyldavis_path)